In [2]:
import pandas as pd, numpy as np

In [3]:
train = pd.read_csv('input/train.csv')
test = pd.read_csv('input/test.csv')
subm = pd.read_csv('input/sample_submission.csv')

COMMENT = 'comment_text'
train[COMMENT].fillna("unknown", inplace=True)
test[COMMENT].fillna("unknown", inplace=True)

In [4]:
train[COMMENT] = train[COMMENT].str.lower()
test[COMMENT] = test[COMMENT].str.lower()

In [5]:
train[COMMENT] = train[COMMENT].str.replace('https?:\/\/[^\s]*','')
test[COMMENT] = test[COMMENT].str.replace('https?:\/\/[^\s]*','')
train[COMMENT] = train[COMMENT].str.replace('=','')
test[COMMENT] = test[COMMENT].str.replace('=','')

In [6]:
train.head()

id                                       comment_text  toxic  \
0  22256635  nonsense?  kiss off, geek. what i said is true...      1   
1  27450690  "\n\n please do not vandalize pages, as you di...      0   
2  54037174  "\n\n ""points of interest"" \n\ni removed the...      0   
3  77493077  asking some his nationality is a racial offenc...      0   
4  79357270  the reader here is not going by my say so for ...      0   

   severe_toxic  obscene  threat  insult  identity_hate  
0             0        0       0       0              0  
1             0        0       0       0              0  
2             0        0       0       0              0  
3             0        0       0       0              0  
4             0        0       0       0              0

In [7]:
train[train['severe_toxic']==1]['comment_text']

213      f'uck you administrators (i will be back to tr...
480      ah haahhahahah yaaa bitch yaaaa!@!!!!!!ah haah...
721      frozen sucks lion king is the bestfrozen sucks...
811                      this user is a fucking douche bag
869      fuck  \n\n62.158.73.165  62.158.73.165  62.158...
1223     fuck you \n\nyou suck. leave me alone. fuck ti...
1563     i am going to shoot you in the head and laugh ...
1695     you're a dirty faggot \n\nlick my hairy nut sa...
1703     stop being a shithead, or i will rip off your ...
1744     and why the fuck you say fuck you up there? fu...
1916     fuck wikipedia and fuck all the leftist, liber...
1951     stop reverting my edit\nyour so fucken gay get...
2030     securityfuck homeland securityfuck homeland se...
2263     are you a fucking dick-head?  people like you ...
2484     fuck you orange suede sof \n\nfuck you orange ...
2492     hello \n\ngo fuck yourself, kid.  adults are t...
2592     fuck you you stupid and gay bastard who thinls.

Prepare FastText training data

In [8]:
label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']
train['clean'] = 1-train[label_cols].max(axis=1)
train.describe()

id         toxic  severe_toxic       obscene        threat  \
count  9.585100e+04  95851.000000  95851.000000  95851.000000  95851.000000   
mean   4.994359e+11      0.096368      0.010068      0.053301      0.003182   
std    2.890136e+11      0.295097      0.099832      0.224635      0.056320   
min    2.225664e+07      0.000000      0.000000      0.000000      0.000000   
25%    2.473437e+11      0.000000      0.000000      0.000000      0.000000   
50%    5.001297e+11      0.000000      0.000000      0.000000      0.000000   
75%    7.501088e+11      0.000000      0.000000      0.000000      0.000000   
max    9.999882e+11      1.000000      1.000000      1.000000      1.000000   

             insult  identity_hate         clean  
count  95851.000000   95851.000000  95851.000000  
mean       0.049713       0.008492      0.897862  
std        0.217352       0.091762      0.302831  
min        0.000000       0.000000      0.000000  
25%        0.000000       0.000000      1.000000  
50%        0.000000       0.000000      1.000000  
75%        0.000000       0.000000      1.000000  
max        1.000000       1.000000      1.000000

In [9]:
from sklearn.model_selection import train_test_split
for label in label_cols:    
    train['label'] = ""
    train.loc[(train[label]==1), 'label'] = "__label__" + label + " "
    train.loc[(train[label]==0), 'label'] = "__label__clean" + " "
    #train_set, val_set = train_test_split(train, test_size=0.2, random_state=1)
    #train_set.to_csv("fasttext_train_"+label+".csv", columns=['label', 'comment_text'], index=False)
    #val_set.to_csv("fasttext_val_"+label+".csv", columns=['label', 'comment_text'], index=False)
    train.to_csv("fasttext_train_"+label+".csv", columns=['label', 'comment_text'], index=False)

In [10]:
train.head()

id                                       comment_text  toxic  \
0  22256635  nonsense?  kiss off, geek. what i said is true...      1   
1  27450690  "\n\n please do not vandalize pages, as you di...      0   
2  54037174  "\n\n ""points of interest"" \n\ni removed the...      0   
3  77493077  asking some his nationality is a racial offenc...      0   
4  79357270  the reader here is not going by my say so for ...      0   

   severe_toxic  obscene  threat  insult  identity_hate  clean  \
0             0        0       0       0              0      0   
1             0        0       0       0              0      1   
2             0        0       0       0              0      1   
3             0        0       0       0              0      1   
4             0        0       0       0              0      1   

             label  
0  __label__clean   
1  __label__clean   
2  __label__clean   
3  __label__clean   
4  __label__clean

# Training
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_identity_hate.csv -output identity_hate -minn 3 -maxn 6 -loss hs
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_insult.csv -output insult -minn 3 -maxn 6 -loss hs
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_obscene.csv -output obscene -minn 3 -maxn 6 -loss hs
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_severe_toxic.csv -output severe_toxic -minn 3 -maxn 6 -loss hs
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_threat.csv -output threat -minn 3 -maxn 6 -loss hs
~/fb_research/fasttext/fastText-0.1.0/fasttext supervised -input  fasttext_train_toxic.csv -output toxic -minn 3 -maxn 6 -loss hs

~/fb_research/fasttext/fastText-0.1.0/fasttext test identity_hate.bin fasttext_val_identity_hate.csv
~/fb_research/fasttext/fastText-0.1.0/fasttext test insult.bin fasttext_val_insult.csv
~/fb_research/fasttext/fastText-0.1.0/fasttext test obscene.bin fasttext_val_obscene.csv
~/fb_research/fasttext/fastText-0.1.0/fasttext test severe_toxic.bin fasttext_val_severe_toxic.csv
~/fb_research/fasttext/fastText-0.1.0/fasttext test threat.bin fasttext_val_threat.csv
~/fb_research/fasttext/fastText-0.1.0/fasttext test toxic.bin fasttext_val_toxic.csv


In [11]:
from pyfasttext import FastText

In [31]:
# https://github.com/facebookresearch/fastText/blob/master/docs/supervised-tutorial.md
# model = FastText()
# model.supervised(input='fasttext_train.csv', output='fasttext_model', epoch=500, lr=0.7)

In [24]:
models = {}
for label in label_cols:
    models[label] = FastText(label+'.bin')
    print(models[label].labels)

['clean', 'toxic']
['clean', 'severe_toxic']
['clean', 'obscene']
['clean', 'threat']
['clean', 'insult']
['clean', 'identity_hate']


In [13]:
models['toxic'] = FastText('toxic.bin')

In [14]:
models['toxic'].predict_proba(["and in the program on last night crime museum: the blackout ripper he is called a serial killer not only by experts but by the police who catched him !!!! so get your facts right you retards"], k=2)

[[('clean', 0.7617187582828185), ('toxic', 0.23632815089296544)]]

# predict

In [25]:
comment_ids = []
comments = []
for index, row in test.iterrows():
    comments.append(row['comment_text'])
    comment_ids.append(row['id'])

predict_probas = {}
for label in label_cols:
    predict_probas[label] = models[label].predict_proba(comments,k=2)   

In [26]:
import csv
with open('submit.csv', "w") as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    writer.writerow(['id','toxic','severe_toxic','obscene','threat','insult','identity_hate'])
    csv_rows = []
    for index, comment_id in enumerate(comment_ids):
        print('processing',index)
        prob_dict = {}        
        #print(comments[index])
        for label in label_cols:       
            #print(predict_probas[label][index])            
            for label_predict, prob in predict_probas[label][index]:                
                if label_predict != 'clean':    
                    prob_dict[label] = prob
        csv_row=[]
        csv_row.append(comment_id)
        
        for label in label_cols:
            if label in prob_dict:
                csv_row.append(prob_dict[label])
            else:
                csv_row.append(0)
        csv_rows.append(csv_row)    
    writer.writerows(csv_rows)

processing 0
processing 1
processing 2
processing 3
processing 4
processing 5
processing 6
processing 7
processing 8
processing 9
processing 10
processing 11
processing 12
processing 13
processing 14
processing 15
processing 16
processing 17
processing 18
processing 19
processing 20
processing 21
processing 22
processing 23
processing 24
processing 25
processing 26
processing 27
processing 28
processing 29
processing 30
processing 31
processing 32
processing 33
processing 34
processing 35
processing 36
processing 37
processing 38
processing 39
processing 40
processing 41
processing 42
processing 43
processing 44
processing 45
processing 46
processing 47
processing 48
processing 49
processing 50
processing 51
processing 52
processing 53
processing 54
processing 55
processing 56
processing 57
processing 58
processing 59
processing 60
processing 61
processing 62
processing 63
processing 64
processing 65
processing 66
processing 67
processing 68
processing 69
processing 70
processing 71
pr

processing 1072
processing 1073
processing 1074
processing 1075
processing 1076
processing 1077
processing 1078
processing 1079
processing 1080
processing 1081
processing 1082
processing 1083
processing 1084
processing 1085
processing 1086
processing 1087
processing 1088
processing 1089
processing 1090
processing 1091
processing 1092
processing 1093
processing 1094
processing 1095
processing 1096
processing 1097
processing 1098
processing 1099
processing 1100
processing 1101
processing 1102
processing 1103
processing 1104
processing 1105
processing 1106
processing 1107
processing 1108
processing 1109
processing 1110
processing 1111
processing 1112
processing 1113
processing 1114
processing 1115
processing 1116
processing 1117
processing 1118
processing 1119
processing 1120
processing 1121
processing 1122
processing 1123
processing 1124
processing 1125
processing 1126
processing 1127
processing 1128
processing 1129
processing 1130
processing 1131
processing 1132
processing 1133
processi

processing 2072
processing 2073
processing 2074
processing 2075
processing 2076
processing 2077
processing 2078
processing 2079
processing 2080
processing 2081
processing 2082
processing 2083
processing 2084
processing 2085
processing 2086
processing 2087
processing 2088
processing 2089
processing 2090
processing 2091
processing 2092
processing 2093
processing 2094
processing 2095
processing 2096
processing 2097
processing 2098
processing 2099
processing 2100
processing 2101
processing 2102
processing 2103
processing 2104
processing 2105
processing 2106
processing 2107
processing 2108
processing 2109
processing 2110
processing 2111
processing 2112
processing 2113
processing 2114
processing 2115
processing 2116
processing 2117
processing 2118
processing 2119
processing 2120
processing 2121
processing 2122
processing 2123
processing 2124
processing 2125
processing 2126
processing 2127
processing 2128
processing 2129
processing 2130
processing 2131
processing 2132
processing 2133
processi

processing 3321
processing 3322
processing 3323
processing 3324
processing 3325
processing 3326
processing 3327
processing 3328
processing 3329
processing 3330
processing 3331
processing 3332
processing 3333
processing 3334
processing 3335
processing 3336
processing 3337
processing 3338
processing 3339
processing 3340
processing 3341
processing 3342
processing 3343
processing 3344
processing 3345
processing 3346
processing 3347
processing 3348
processing 3349
processing 3350
processing 3351
processing 3352
processing 3353
processing 3354
processing 3355
processing 3356
processing 3357
processing 3358
processing 3359
processing 3360
processing 3361
processing 3362
processing 3363
processing 3364
processing 3365
processing 3366
processing 3367
processing 3368
processing 3369
processing 3370
processing 3371
processing 3372
processing 3373
processing 3374
processing 3375
processing 3376
processing 3377
processing 3378
processing 3379
processing 3380
processing 3381
processing 3382
processi

processing 4336
processing 4337
processing 4338
processing 4339
processing 4340
processing 4341
processing 4342
processing 4343
processing 4344
processing 4345
processing 4346
processing 4347
processing 4348
processing 4349
processing 4350
processing 4351
processing 4352
processing 4353
processing 4354
processing 4355
processing 4356
processing 4357
processing 4358
processing 4359
processing 4360
processing 4361
processing 4362
processing 4363
processing 4364
processing 4365
processing 4366
processing 4367
processing 4368
processing 4369
processing 4370
processing 4371
processing 4372
processing 4373
processing 4374
processing 4375
processing 4376
processing 4377
processing 4378
processing 4379
processing 4380
processing 4381
processing 4382
processing 4383
processing 4384
processing 4385
processing 4386
processing 4387
processing 4388
processing 4389
processing 4390
processing 4391
processing 4392
processing 4393
processing 4394
processing 4395
processing 4396
processing 4397
processi

...

processing 221098
processing 221099
processing 221100
processing 221101
processing 221102
processing 221103
processing 221104
processing 221105
processing 221106
processing 221107
processing 221108
processing 221109
processing 221110
processing 221111
processing 221112
processing 221113
processing 221114
processing 221115
processing 221116
processing 221117
processing 221118
processing 221119
processing 221120
processing 221121
processing 221122
processing 221123
processing 221124
processing 221125
processing 221126
processing 221127
processing 221128
processing 221129
processing 221130
processing 221131
processing 221132
processing 221133
processing 221134
processing 221135
processing 221136
processing 221137
processing 221138
processing 221139
processing 221140
processing 221141
processing 221142
processing 221143
processing 221144
processing 221145
processing 221146
processing 221147
processing 221148
processing 221149
processing 221150
processing 221151
processing 221152
processing

processing 222277
processing 222278
processing 222279
processing 222280
processing 222281
processing 222282
processing 222283
processing 222284
processing 222285
processing 222286
processing 222287
processing 222288
processing 222289
processing 222290
processing 222291
processing 222292
processing 222293
processing 222294
processing 222295
processing 222296
processing 222297
processing 222298
processing 222299
processing 222300
processing 222301
processing 222302
processing 222303
processing 222304
processing 222305
processing 222306
processing 222307
processing 222308
processing 222309
processing 222310
processing 222311
processing 222312
processing 222313
processing 222314
processing 222315
processing 222316
processing 222317
processing 222318
processing 222319
processing 222320
processing 222321
processing 222322
processing 222323
processing 222324
processing 222325
processing 222326
processing 222327
processing 222328
processing 222329
processing 222330
processing 222331
processing

processing 223769
processing 223770
processing 223771
processing 223772
processing 223773
processing 223774
processing 223775
processing 223776
processing 223777
processing 223778
processing 223779
processing 223780
processing 223781
processing 223782
processing 223783
processing 223784
processing 223785
processing 223786
processing 223787
processing 223788
processing 223789
processing 223790
processing 223791
processing 223792
processing 223793
processing 223794
processing 223795
processing 223796
processing 223797
processing 223798
processing 223799
processing 223800
processing 223801
processing 223802
processing 223803
processing 223804
processing 223805
processing 223806
processing 223807
processing 223808
processing 223809
processing 223810
processing 223811
processing 223812
processing 223813
processing 223814
processing 223815
processing 223816
processing 223817
processing 223818
processing 223819
processing 223820
processing 223821
processing 223822
processing 223823
processing

processing 225276
processing 225277
processing 225278
processing 225279
processing 225280
processing 225281
processing 225282
processing 225283
processing 225284
processing 225285
processing 225286
processing 225287
processing 225288
processing 225289
processing 225290
processing 225291
processing 225292
processing 225293
processing 225294
processing 225295
processing 225296
processing 225297
processing 225298
processing 225299
processing 225300
processing 225301
processing 225302
processing 225303
processing 225304
processing 225305
processing 225306
processing 225307
processing 225308
processing 225309
processing 225310
processing 225311
processing 225312
processing 225313
processing 225314
processing 225315
processing 225316
processing 225317
processing 225318
processing 225319
processing 225320
processing 225321
processing 225322
processing 225323
processing 225324
processing 225325
processing 225326
processing 225327
processing 225328
processing 225329
processing 225330
processing

processing 226276
processing 226277
processing 226278
processing 226279
processing 226280
processing 226281
processing 226282
processing 226283
processing 226284
processing 226285
processing 226286
processing 226287
processing 226288
processing 226289
processing 226290
processing 226291
processing 226292
processing 226293
processing 226294
processing 226295
processing 226296
processing 226297
processing 226298
processing 226299
processing 226300
processing 226301
processing 226302
processing 226303
processing 226304
processing 226305
processing 226306
processing 226307
processing 226308
processing 226309
processing 226310
processing 226311
processing 226312
processing 226313
processing 226314
processing 226315
processing 226316
processing 226317
processing 226318
processing 226319
processing 226320
processing 226321
processing 226322
processing 226323
processing 226324
processing 226325
processing 226326
processing 226327
processing 226328
processing 226329
processing 226330
processing

In [22]:
pred = pd.read_csv('submit.csv')

In [23]:
pred.loc[pred['severe_toxic'] > 0.8]

id     toxic  severe_toxic   obscene        threat  \
2073      9152726631  1.000000      0.898438  1.000000  4.296877e-02   
2291     10093563914  0.001953      0.998047  0.162109  3.417969e-01   
2991     13207123035  1.000000      0.857422  1.000000  2.636719e-01   
3221     14282370093  1.000000      0.859375  1.000000  5.878906e-01   
5727     25308734743  1.000000      0.960937  1.000000  6.445314e-02   
6037     26465568197  1.000000      0.894531  1.000000  2.148440e-02   
6427     28018151504  1.000000      0.960937  1.000000  1.093750e-01   
6507     28410502015  1.000000      0.890625  1.000000  1.953127e-08   
6551     28661663728  1.000000      0.902344  1.000000  5.664065e-02   
7897     34528220435  1.000000      0.947266  1.000000  1.894531e-01   
8357     36821998592  0.998047      0.927734  0.998047  1.738281e-01   
9557     41900253509  1.000000      0.964844  1.000000  4.199219e-01   
10042    44110442201  1.000000      0.998047  1.000000  1.660156e-01   
10554    46315235525  0.998047      0.902344  0.998047  5.390625e-01   
12096    53183071356  1.000000      0.988281  1.000000  2.714844e-01   
12491    54834913937  1.000000      0.998047  1.000000  2.460938e-01   
12513    54925324405  1.000000      0.951172  1.000000  1.953127e-08   
12635    55566589767  1.000000      0.962891  1.000000  3.906270e-03   
13242    58348590487  1.000000      0.890625  1.000000  1.953127e-08   
13823    60895613393  0.998047      0.982422  0.998047  2.031250e-01   
13996    61710168712  1.000000      0.982422  1.000000  5.664065e-02   
14114    62233829263  0.998047      0.826172  0.998047  4.140625e-01   
14174    62499818599  1.000000      0.998047  1.000000  9.179691e-02   
14425    63564038830  0.998047      0.970703  0.023438  1.562500e-01   
15087    66310248454  1.000000      0.990234  1.000000  9.570314e-02   
16509    72559176431  1.000000      0.902344  1.000000  1.699219e-01   
16582    72900199691  0.861328      0.804687  0.455078  3.164063e-01   
17253    75859090464  1.000000      0.988281  1.000000  4.804688e-01   
18519    81411763541  0.998047      0.849609  0.998047  3.339844e-01   
20889    92115820405  0.998047      0.964844  0.998047  6.894531e-01   
...              ...       ...           ...       ...           ...   
212665  937412071860  1.000000      0.843750  1.000000  3.320314e-02   
213355  940197022309  1.000000      0.996094  1.000000  7.500000e-01   
213883  942591144664  0.181641      0.857422  0.435547  7.031252e-02   
214060  943363098825  1.000000      0.890625  1.000000  1.953127e-08   
214226  944130992800  0.769531      0.957031  0.744141  2.617188e-01   
214693  946083055427  1.000000      0.998047  1.000000  2.597657e-01   
215059  947722625790  0.998047      0.921875  0.998047  9.375002e-02   
215574  949951894431  1.000000      0.919922  1.000000  1.171877e-02   
215648  950288532080  0.998047      1.000000  0.998047  2.656250e-01   
215851  951155995281  1.000000      0.964844  1.000000  4.882814e-02   
216038  951956719665  0.996094      0.833984  0.982422  2.734375e-01   
216868  955418733642  1.000000      0.994141  1.000000  1.425781e-01   
217177  956863985471  1.000000      0.912109  1.000000  2.421875e-01   
218283  961940159482  1.000000      0.931641  1.000000  4.492188e-01   
218901  964550394243  1.000000      0.960937  1.000000  2.714844e-01   
218909  964579383320  1.000000      0.996094  1.000000  1.738281e-01   
219505  967111090014  1.000000      0.962891  1.000000  3.906270e-03   
219506  967111385179  0.998047      0.892578  1.000000  4.179688e-01   
219977  969214153774  1.000000      0.986328  1.000000  2.656250e-01   
220295  970666653034  1.000000      0.962891  1.000000  3.906270e-03   
221469  975825510091  1.000000      0.996094  1.000000  2.539064e-02   
222595  980585067702  1.000000      0.982422  1.000000  2.402344e-01   
223278  983662313846  1.000000      0.972656  1.000000  5.664065e-02   
223295  983727251915  1.000000      0.962891  1.000000  3.

In [118]:
test.loc[test['id'] == 787050824879]['comment_text']

201691    == credit ==
Name: comment_text, dtype: object